# Add transaction_value_SGD into MongoDB.Transaction

## Connect to database

In [9]:
from pymongo import MongoClient
import mysql.connector
from datetime import datetime


# MongoDB setup
mongo_client = MongoClient('mongodb://localhost:27017/')
mongo_db = mongo_client['Coinut']
collection = mongo_db['transaction']
# Fetch all doc data
data1 = collection.find()

# MySQL setup
mysql_db = mysql.connector.connect(
  user='root', password='liuwinq1', host='localhost', database='coinut')
mysql_cursor = mysql_db.cursor()

# Index Dictionary
index_dict = {1: 'LTC, BTC', 2: 'ETH, BTC', 3: 'ETC, BTC', 490569: 'ETH, LTC', 490588: 'ETC, LTC', 490589: 'BTC, USDT', 490590: 'LTC, USDT', 490591: 'ETH, USDT', 490592: 'ETC, USDT', 852382: 'XMR, USDT', 852383: 'XMR, BTC', 852384: 'XMR, LTC', 1111976: 'ZEC, USDT', 1111977: 'ZEC, BTC', 1111978: 'ZEC, LTC', 1801843: 'BTC, CAD', 1801844: 'LTC, CAD', 1801845: 'ETH, CAD', 1885998: 'ZEC, CAD', 2372505: 'BTC, XSGD', 2372506: 'LTC, XSGD', 2372507: 'ETH, XSGD', 2372508: 'USDT, XSGD', 2372510: 'DAI, XSGD', 2372511: 'ETC, XSGD', 2372512: 'BTC, XIDR', 852220: 'USDT, USD', 852234: 'LTC, USD', 852379: 'BTC, USD', 852380: 'BTC, SGD', 852381: 'LTC, SGD', 899746: 'USDT, SGD', 1063804: 'ETH, SGD', 1885996: 'ZEC, USD', 1885999: 'ETH, USD', 2372503: 'ETC, SGD', 2372504: 'DAI, SGD', 2372509: 'XSGD, SGD'}

In [10]:
for transaction in data1:
    # Get instId and use it to find the currency pair
    inst_id = transaction['order']['instId']
    pair = index_dict.get(inst_id, None)
    
    if pair:
        # Split the currency pair
        base_currency, second_currency = pair.split(', ')

        # Convert timestamp to date
        timestamp = transaction['timestamp']
        dt = datetime.utcfromtimestamp(int(timestamp) / 1e6).strftime('%Y-%m-%d')

        # Use date to find the first price data for this base currency and SGD of the day
        mysql_cursor.execute(f"SELECT `{base_currency}`, `SGD` FROM price_transformed WHERE DATE = '{dt}' ORDER BY time ASC LIMIT 1")

    
    # Fetch the result
    result = mysql_cursor.fetchone()
    print(result)
   # If we got a result, calculate the value in SGD
    if result is not None:
        base_currency_price, sgd_price = result
        # Calculate the index price
        index_price = base_currency_price / sgd_price

        # Get the fill quantity
        fill_qty = float(transaction['fillQty'])
       
        # Calculate the transaction value in SGD
        transaction_value_sgd = fill_qty * float(index_price)

        # Add the transaction value to the transaction document
        transaction['transaction_value_sgd'] = transaction_value_sgd
        
        print(transaction_value_sgd)
        
        #Check out the value
        #print(transaction_value_sgd)
        # Update the MongoDB document
        #collection.update_one({'_id': transaction['_id']}, {'$set': {'transaction_value_sgd': float(transaction_value_sgd)}})


None
(146.31, 0.74160877)
3.753193803250196
(146.31, 0.74160877)
0.09963009202277907
(146.31, 0.74160877)
0.2959309664042943
(146.31, 0.74160877)
0.2951418171605495
(3706.42, 0.74160877)
249.89051841984016
(3706.42, 0.74160877)
84.96277626274565
(3706.42, 0.74160877)
79.96496589434885
(46724.07, 0.74160877)
63.003664317508004
(154.61, 0.74160877)
0.10007001400482361
(146.31, 0.74160877)
0.09469790924937417
(3706.42, 0.74160877)
549.7591405236483
(46724.07, 0.74160877)
63.003664317508004
(33.67, 0.74160877)
0.0499414266635493
(33.67, 0.74160877)
0.0499414266635493
(146.31, 0.74160877)
0.22194822480322068
(3706.42, 0.74160877)
0.04997810368396803
(146.31, 0.74160877)
59.10846208034999
(233.61, 0.74160877)
63.57229100729216
(233.61, 0.74160877)
65.22007884291875
(46724.07, 0.74160877)
63.003664317508004
(1.0, 0.74160877)
67.42099341678497
(1.0, 0.74160877)
1422.5830150309575
(233.61, 0.74160877)
0.4337610112135001
(233.61, 0.74160877)
63.456369400809535
(233.61, 0.74160877)
65.70424055260

(1.0, 0.73893252)
230.13603461382377
(148.95, 0.73893252)
0.19996196675712688
(1.0, 0.73893252)
375.5417341762141
(1.0, 0.73893252)
737.5504328866188
(3768.86, 0.73893252)
16.127501493641127
(34.68, 0.73893252)
0.004693256699542741
(148.95, 0.73893252)
0.07800935598287106
(148.95, 0.73893252)
0.30236184489484913
(148.95, 0.73893252)
0.30236184489484913
(148.95, 0.73893252)
0.19976039219386363
(46500.42, 0.73893252)
44.05042831245267
(46500.42, 0.73893252)
18.878754991051142
(148.95, 0.73893252)
0.0060472368978969826
(236.46, 0.73893252)
67.324613727922
(34.68, 0.73893252)
0.0018773026798170965
(148.95, 0.73893252)
0.004031491265264655
(148.95, 0.73893252)
0.0038299167020014223
(148.95, 0.73893252)
143.80530917762286
(34.68, 0.73893252)
0.0018303701128216689
(148.95, 0.73893252)
0.40314912652646545
(46500.42, 0.73893252)
3.8386801815137326
(148.95, 0.73893252)
0.47269235085228073
(148.95, 0.73893252)
0.19814779568775776
(148.95, 0.73893252)
276.95639481396756
(148.95, 0.73893252)
118.74

(135.02, 0.73849692)
3557.450493036586
(1.0, 0.73849692)
94.78712517853154
(216.13, 0.73849692)
0.029558863969263403
(135.02, 0.73849692)
0.1462646587612038
(43435.72, 0.73849692)
0.11763277225313276
(216.13, 0.73849692)
0.029266201949765747
(216.13, 0.73849692)
68.40038187295352
(1.0, 0.73849692)
0.00012186916094382628
(135.02, 0.73849692)
245.06625292357347
(30.88, 0.73849692)
0.21116404926915602
(3536.48, 0.73849692)
131.14481409076157
(3536.48, 0.73849692)
730.2849685547775
(3536.48, 0.73849692)
215.4939251473114
(3536.48, 0.73849692)
344.1916859991779
(3536.48, 0.73849692)
963.377564255786
(3536.48, 0.73849692)
20.50065541234756
(3536.48, 0.73849692)
152.69899535938484
(3536.48, 0.73849692)
592.7711117874398
(135.02, 0.73849692)
0.07678894584963199
(135.02, 0.73849692)
0.07642328420272898
(135.02, 0.73849692)
0.07678894584963199
(135.02, 0.73849692)
23.768007048695615
(135.02, 0.73849692)
118.03137451135206
(43435.72, 0.73849692)
14.880545690021295
(43435.72, 0.73849692)
43.935840

(3414.47, 0.7350563)
345.66189842873257
(3414.47, 0.7350563)
769.2978152013661
(200.97, 0.7350563)
74.20665815666092
(43114.05, 0.7350563)
299.42907128338334
(43114.05, 0.7350563)
733.1759825743961
(43114.05, 0.7350563)
89.44746987407632
(3414.47, 0.7350563)
298.6387250881327
(3414.47, 0.7350563)
371.54485030602416
(3414.47, 0.7350563)
690.1346303677691
(43114.05, 0.7350563)
963.7451655743922
(136.0, 0.7350563)
264.4083398781835
(31.04, 0.7350563)
99.26114622784677
(31.04, 0.7350563)
99.26114622784677
(136.0, 0.7350563)
0.3700396826746468
(136.0, 0.7350563)
0.36911458346796017
(43114.05, 0.7350563)
144.6996119208828
(136.0, 0.7350563)
0.0037003968267464685
(43114.05, 0.7350563)
73.3175982574396
(43114.05, 0.7350563)
30.265504560671065
(43114.05, 0.7350563)
41.35112541719594
(43114.05, 0.7350563)
44.45979158331138
(43114.05, 0.7350563)
100.29847441617737
(43114.05, 0.7350563)
140.769788654284
(1.0, 0.7350563)
1989.6435143811432
(136.0, 0.7350563)
0.011101190480239406
(1.0, 0.7350563)
0.

(41794.62, 0.73662362)
482.16032057185464
(41794.62, 0.73662362)
1049.7682103107147
(41794.62, 0.73662362)
230.81056531964043
(30.67, 0.73662362)
0.8077367923662291
(131.8, 0.73662362)
0.008946224124607898
(3206.71, 0.73662362)
707.5736136318842
(3206.71, 0.73662362)
727.676942357618
(138.42, 0.73662362)
5.783350172778873
(1.0, 0.73662362)
0.006977783308116022
(41794.62, 0.73662362)
0.1134761874727829
(41794.62, 0.73662362)
0.39716665615474017
(3206.71, 0.73662362)
768.16656134377
(3206.71, 0.73662362)
667.0839946457323
(131.8, 0.73662362)
0.17892448249215795
(3206.71, 0.73662362)
659.457092972392
(131.8, 0.73662362)
0.0017892448249215796
(3206.71, 0.73662362)
435.32543797604535
(3206.71, 0.73662362)
224.13165499634667
(131.8, 0.73662362)
0.003578489649843159
(41794.62, 0.73662362)
1029.229020378141
(41794.62, 0.73662362)
1029.909877502978
(131.8, 0.73662362)
2.7887169841227735
(41794.62, 0.73662362)
56.738093736391455
(41635.34, 0.73774573)
5.7000253190215
(3062.49, 0.73774573)
4.9274

...

(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.23168542468023545
(17.69, 0.74062924)
0.23646244374580733
(17.69, 0.74062924)
0.23646244374580733
(17.69, 0.74062924)
0.24123946281137917
(17.69, 0.74062924)
0.12659100523765443
(1

(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.1170369671065107
(17.

(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.1170369671065107
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.11942547663929663
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12420249570486848
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.12659100523765443
(17.69, 0.74062924)
0.10748292897536696
(17.69, 0.74062924)
0.01910807626228746
(17.69, 0.74062924)
0.12181398617208257
(17.69, 0.74062924)
0.11942547663929663
(1

(17.69, 0.73882469)
0.24422302400316376
(17.69, 0.73882469)
0.24422302400316376
(17.69, 0.73882469)
0.004788686745160074
(17.69, 0.73882469)
0.12929454211932198
(17.69, 0.73882469)
0.12690019874674194
(17.69, 0.73882469)
0.1173228252564218
(17.69, 0.73882469)
0.12450585537416191
(17.69, 0.73882469)
0.004788686745160074
(17.69, 0.73882469)
0.05746424094192088
(17.69, 0.73882469)
0.06704161443224103
(17.69, 0.73882469)
0.12211151200158188
(17.69, 0.73882469)
0.12690019874674194
(17.69, 0.73882469)
0.12211151200158188
(17.69, 0.73882469)
0.12690019874674194
(17.69, 0.73882469)
0.12450585537416191
(17.69, 0.73882469)
0.2466173673757438
(17.69, 0.73882469)
0.24422302400316376
(17.69, 0.73882469)
0.2514060541209039
(17.69, 0.73882469)
0.24182868063058371
(17.69, 0.73882469)
0.24422302400316376
(17.69, 0.73882469)
0.24901171074832382
(17.69, 0.73882469)
0.11971716862900184
(17.69, 0.73882469)
0.13168888549190202
(17.69, 0.73882469)
0.11013979513868169
(17.69, 0.73882469)
0.13887191560964213
(

(92.21, 0.73980669)
22.28238613251794
(92.21, 0.73980669)
22.2600754529538
(92.21, 0.73980669)
22.195511586952534
(92.21, 0.73980669)
11.151849843369218
(92.21, 0.73980669)
11.021475704687125
(92.21, 0.73980669)
22.109010963390993
(92.21, 0.73980669)
22.086949565162758
(92.21, 0.73980669)
22.022884261833315
(92.21, 0.73980669)
22.000822863605087
(92.21, 0.73980669)
11.043412462247401
(92.21, 0.73980669)
10.893594379364156
(92.21, 0.73980669)
21.915070084051283
(92.21, 0.73980669)
21.851503343393663
(92.21, 0.73980669)
21.829691226501343
(92.21, 0.73980669)
21.76637376717964
(92.21, 0.73980669)
21.74456165028732
(92.21, 0.73980669)
10.87228082514366
(92.21, 0.73980669)
10.810459053837429
(92.21, 0.73980669)
21.661052402756724
(92.21, 0.73980669)
10.87228082514366
(92.21, 0.73980669)
10.725952680963186
(92.21, 0.73980669)
10.852213677602727
(92.21, 0.73980669)
10.724456992947712
(92.21, 0.73980669)
21.5188374006188
(92.21, 0.73980669)
21.497274565062394
(92.21, 0.73980669)
21.44691973520

# Checkout